# AST416 Astronomide Sayısal Çözümleme - II #
## Ders - 01b Bilgisayarda Sayıların Temsili ve Yuvarlama Problemleri ile Python Çözümleri ##

Doç. Dr. Özgür Baştürk <br>
Ankara Üniversitesi, Astronomi ve Uzay Bilimleri Bölümü <br>
obasturk at ankara.edu.tr <br>
http://ozgur.astrotux.org

# Bu derste neler öğreneceksiniz?#
## Bilgisayarda Sayıların Temsili ve Yuvarlama Problemleri ile Python Çözümleri ##

* [Yuvarlama Yanlışları](#Yuvarlama-Yanlışları)
* [Kayan Noktalı Sayılar](#Kayan-Noktalı-Sayılar)
* [Sayı Sistemlerindeki Temsil Sorunları](#Sayı-Sistemlerindeki-Temsil-Sorunları)
* [Kesme ve Yuvarlama İşlemleri](#Kesme-ve-Yuvarlama-İşlemleri)
    * [Makine Epsilonu](#Makine-Epsilonu)
    * [ Aritmetik İşlemlerin Getirdiği Kesme ve Yuvarlama Yanlışları](#Aritmetik-İşlemlerin-Getirdiği-Kesme-ve-Yuvarlama-Yanlışları)
        * [1 Toplama ve Çıkarma](#1-Toplama-ve-Çıkarma)
        * [2 Çarpma ve Bölme](#2-Çarpma-ve-Bölme)
        * [3 Büyük ve Küçük Sayıyla Toplama Çıkarma](#3-Büyük-ve-Küçük-Sayıyla-Toplama-Çıkarma)
        * [4 Yakın İki Sayıyı Çıkarma](#4-Yakın-İki-Sayıyı-Çıkarma)
* [Python'da Kayan Noktalı Sayılar](#Python'da-Kayan-Noktalı-Sayılar)
* [Decimal Modülü](#Decimal-Modülü)
    * [Decimal Modülünde Yuvarlama Seçenekleri](#Decimal-Modülünde-Yuvarlama-Seçenekleri)
* [Numpy Modülünde Yuvarlama Seçenekleri](#Numpy-Modülünde-Yuvarlama-Seçenekleri)
* [Pandas Modülünde Yuvarlama Seçenekleri](#Pandas-Modülünde-Yuvarlama-Seçenekleri)
* [Kaynaklar](#Kaynaklar)

# Yuvarlama Yanlışları #

Yuvarlama konusunun ayrıntlı olarak anlatıldığı [Hata Analizi](Ders01_Hata_Analizi_Uygulamalar.html) dersinde ayrıntılı olarak verildiği gibi Yuvarlama yanlışları temelde iki problemden kaynaklanır:

1. $\pi$, $e$, $\sqrt{7}$ gibi sayılar sabit sayıda anlamlı rakamla temsil edilemezler. Bu nedenle bilgisayarlar da bu sayıları tam olarak temsil edemez. 

2. Bilgisayarlar ikilik sayı sistemini kullandıklarından onluk sayı sistemine dayalı tüm sayıları aynı duyarlılıkta temsll edemezler.

Yuvarlama işlemi kaynaklı hatalar sayıların bilgisayarda tutulma şekline doğrudan bağlıdır. 10 parmağımız olduğu için onluk sayı sistemi biz insanlar için “doğal” olandır. Bir bilgisayar ise sadece 2 parmağı olan bir varlık gibi düşünülebilir. Bu nedenle ikilik sayı sistemi de onun için “doğal” olandır.  

Herhangi bir sayıyı onluk ve ikilik sayı sistemlerinde  aşağıdaki şekillerde çözümlenir (Chapra & Canale 2009). 

In [ ]:
from IPython.display import Image
Image(filename='images/sayi_sistemleri.png', width=400)

Bu durum her iki sayı sisteminde ve diğer tüm sayı sistemlerinde sayıların mükemmel temsil edilemiyor olmasına yol açar. Buna ek olarak bilgisayarlar sınırlı kapasiteleri nedeniyle sadece belirli bir sayı aralığını temsil edebilirler. Örneğin 16 bitlik bir sayı sistemi varsayılan olarak -32768 ile 32767 arasındaki tam sayıları saklayabilir. 16 bitlik CCD dedektörlerde algılanan fotonların ADU biriminden karşılığının 0-65535 arasında olbilmesinin nedeni de budur. Foton algılama işlemi doğası gereği bir "sayım" işlemi olduğundan negatif sayılara ihtiyaç duyulmaz.

In [ ]:
from IPython.display import Image
Image(filename='images/sayi_sistemleri_16bit.png', width=400)

Yukarıdaki şekilde şematik olarak gördüğünüz 16 bit ikilik sayı sisteminde, her bir basamak sadece 0 veya 1 değerini alabilir ve toplamda 16 basamak vardır. 1. basamak işaret için ayrılır ve 0 iki kere sayılmaz. En baştaki 0: pozitif, 1: negatif sayıları ifade eder. Bu durumda yazılabilecek en küçük sayı $1111111111111111$ (bu sayının onluk sayı sistemindeki karşılığı -32767 olduğu halde 0'ı iki kez saymamak için onu pozitif sayılara dahil edip saymaya -1'den başladığımız için -32768) olurken en büyük sayı $0111111111111111$ (32767) olur. 

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Kayan Noktalı Sayılar #

Bilgisayarlar tam sayılar dışındaki sayıları göstermek üzere kayan noktalı sayıları (ing. floating point numbers) kullanırlar. Aşağıda kayan noktaları sayıların hafızada saklanma şeklini örnekleyen bir şekil bulunmaktadır. Herhangi bir sayı bu şekilde m: mantis, b: taban, e: üssü göstermek üzere

$$ m~b^e $$

şeklinde ifade edilir.

In [ ]:
from IPython.display import Image
Image(filename='images/sayi_sistemleri_floatingpoint.png', width=400)

Örneğin onluk sayı sistemindeki $156.78$ sayısını düşünelim. Bu sayıyı bilimsel gösterimde (ing. scientific notation) şu şekilde ifade edebiliriz: $0.15678 x 10^{3}$.

Eğer mantis başında gereksiz $0$ sayıları varsa <b><i>normalize</i></b> edilebilir. Örneğin,  $1 / 34 = 0.029411765...$ sadece 4 basamağa izin verilen 10'luk bir kayan sayı sisteminde $0.0294 x 10^0$ şeklinde saklanabilir. Ancak bu şekilde noktadan sonraki 0 nedeniyle 5. basamaktaki $1$ sayısını kaybetmiş oluruz. Bunu sayıyı $0.2941 x 10^{-1}$ şeklinde göstererek aşabiliriz. Noktanın bu şekilde kaydırılması bu sayıların <b>"kayan noktalı sayılar”</b> (ing. floating point numbers) olarak adlandırılmış olmasının da kaynağıdır. Böylece noktadan sonra gelen gereksiz 0'a da izin verilmemiş olur. Bu işleme <b>normalizasyon</b> adı verilir ve sayılarda anlamsız rakamların elenmesi işlevini de görür.

Normalizasyonun doğal bir sonucu mantis (m) için limitli bir değer aralığına sahip olunmasıdır. b, tabanı; m, mantisi göstermek üzere

$$\frac{1}{b} \le m \lt 1$$

Örneğin onluk sayı sisteminde 

$$0.1  \le m \lt 1$$ iken ikilik sayı sisteminde 

$$ 0.5 \le m \lt 1$$  

<b>Örnek: </b> Yedi bitlik ikilik bir sayı sistemini ele alalım (Şekil Chapra & Canale 2009'dan alınmış ve Türkçeleştirilmiştir) ve bu sayı sisteminde ifade edilebilecek en büyük ve en küçük sayıları hesaplamak istiyor olalım.

In [ ]:
from IPython.display import Image
Image(filename='images/sayi_sistemleri_7bit.png', width=300)

Bu sistemde ifade edebileceğimiz en küçük poziftif sayı $011100$ 'dir. bu sayının onluk sayı sistemindeki karşılığı $m = 1x2^{-1} + 0x2^{-2} + 0x2^{-3} = 0.5$, $b=2$ , $e = -(1x2^0 + 1x2^1) = -3$ olduğundan 

$$ - (1x2^{-1} + 0x2^{-2} + 0x2^{-3}) x 2^{-(1x2^1+1x2^0)} = -0.5 x 2^{-3} = -0.0675 $$

sayısıdır. 

En büyük poziftif sayı ise $0011111$ sayısı olup onluk sayı sistemindeki karşılığı $m = 1x2^{-1} + 1x2^{-2} + 1x2^{-3} = 0.875$, $b=2$ , $e = 1x2^0 + 1x2^1 = 3$ olduğundan 

$$ 1x2^{-1} + 1x2^{-2} + 1x2^{-3}) x 2^{1x2^1 + 1x2^0} = 0.875 x 2^{3} = 7 $$

sayısıdır.

Aslında bu sayı sisteminde daha küçük mantisler yazabiliriz ($000$, $001$, $010$, $011$) ancak normalizsyon gereği noktadan sonraki gereksiz $0$'ları atmaya yönelik bir işlem uygulanacağından buna izin verilmez. Dolayısı ile en küçük olarak ifade edilebilien bu sayıyı aşağıdaki sayılar takip eder:

$$ 0111101 = (1 x 2^{−1} + 0 x 2^{−2} + 1x2^{−3}) x 2^{−3} = (0.078125)_{10} $$
$$ 0111101 = (1 x 2^{−1} + 1 x 2^{−2} + 0x2^{−3}) x 2^{−3} = (0.093750)_{10} $$	
$$ 0111101 = (1 x 2^{−1} + 1 x 2^{−2} + 1x2^{−3}) x 2^{−3} = (0.109375)_{10} $$	

Bu sayı sistemiyle $0.0625$ sayısından küçük sayıların temsil edilememesinin yanı sıra her sayının da temsil edilemediğine dikkat ediniz. Sayılar $0.015625$ aralıkla artmakta, bu artışın altındaki artışlarla ulaşılacak sayılar gösterilememektedir! Bu noktadan sonra sayıyı büyütmek için üssü büyütmeliyiz!

$$ 0110100 = (1 x 2^{−1} + 0 x 2^{−2} + 0x2^{−3}) x 2^{−2} (0.125000)_{10} $$
$$ 0110101 = (1 x 2^{−1} + 0 x 2^{−2} + 1x2^{−3}) x 2^{−2} = (0.156250)_{10} $$
<center>
...<br>
...<br>
...<br>
</center>
$$ 0011111 = (1 x 2^{−1} + 0 x 2^{−2} + 1x2^{−3}) x 2^{3} = (7)_{10} $$

Görüldüğü üzere sayılar büyüdükçe aralarındaki farklar da artmakta ve tam olarak temsil edilemeyen sayıların sayısı da buna bağlı olarak artmaktadır. Ayrıca 7 sayısının üstündeki sayılar da bu sayı sisteminde temsil edilememektedir. 7 bitlik sayı sistemi kuşkusuz modern bilgisayarlarda kullanılan 32 bit ve 64 bitlik sayı sistemleriyle karşılaştırıldığında son derece basit ve kullanışsız ve bir sistemdir. Ancak onlarda karşılaşılan güçlükleri örneklemek açısından faydaldır.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Sayı Sistemlerinde Temsil Sorunları ve Sonuçları #

Yukarıdaki örneklerden çıkarsanması gereken dört temel sonuç:

1. Sadece belirlii bir aralıktaki sayılar temsil edilebilir. Tıpkı tam sayıda olduğu gibi ($-32768 – 32767$) kayan noktalı sayı gösteriminde de çok büyük pozitif ve çok küçük negatif sayıların temsili sorunu vardır. Bu sınırların dışına çıkmaya kalkarsanız <b>taşma (overflow)</b> hatası alırsınız. 

2. Normalizasyon nedeniyle çok küçük pozitif sayıların gösterimiyle de ilgili bir problem yaşanır. Bu problem 0'dan sonra ilk temsil edilebilen sayıya kadar büyük bir boşluğun <i>(underflow)</i> oluşmasına neden olur.

3. Tüm nicelikler temsil edilemezler! Bu nedenle hassasiyet de sınırlıdır. Açık ki irrasyonel sayılar tam olarak temsil edilemezler. Ayrıca temsil edilebilen küme dışında kalan rasyonel sayılar da tam olarak temsil edilemezler. Bu sorun <b>kuantizasyon hatası (quantization error)</b> olarak bilinen hataya yol açar.

4. Temsil edilmek istenen sayı büyüdükçe temsil edilebilen sayılar arasındaki uzaklığın da artmasıdır (64 bitlik sayı sisteminde $1.0$ ile $2.0$ arasında  $8~388~607$ tane kayan noktalı sayı varken $1023$ ile $1024$ arasında sadece $8191$ tane vardır).

<b>Çözüm:</b> Temsil edemediğniz basamakları ya keser atarsınız (<i>ing. truncation</i>) ya da yuvarlarsınız (<i>rounding</i>)! 

In [ ]:
from IPython.display import Image
Image(filename='images/sayi_sistemleri_yuvarlama_kesme.png', width=500)

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Kesme ve Yuvarlama İşlemleri #

<i>“Kırpma”</i> ya da <b>kesme (truncation, chopping)</b> işlemi uygulanırsa, şekilden de görüleceği gibi sondan atılan $\Delta x$ kadar hata yapılmış olur. Bu durumda yapılan hata her zaman pozitiftir. Örneğin $\pi = 3.14159265358...$ sayısına bakalım. Sayımız 6. basamaktan sonra temsil edilemiyor olsun. Bu durumda kesme işi uygularsak sayı $\pi ~ 3.141592$ şeklinde ifade edilir ve hatası $|\epsilon_t = 0.00000065...$ olur. Oysa ki yuvarlama işlemi uygulanmış olsaydı sayı $\pi ~ 3.141593$ şeklinde ifade edilir ve hatası $\epsilon_t = 0.00000035...$ olurdu. Dolaysı ile kesme işleminde hatanın üst sınırı $\Delta x$ iken, yuvarlamada $\Delta x / 2$'dir. Ayrıca yuvarlama işleminden gelen hatada yanlılık da mevcut değildir; pozitif olabileceği gibi negatif de olabilir. Ancak yuvarlama işlemi ek kod gerektirir. Bu ek koddan kaçınmak için, modern bilgisayarların oldukça büyük ve küçük sayıları saklayabiliyor olması gerekçesiyle, kesme işlemine gidilir.

Bir başka problem de  temsil edilmek istenen sayı büyüdükçe temsil edilebilen sayılar arasındaki uzaklığın da artmasıdır. Dolayısı ile kuantizasyon hatası sayının büyüklüğüne bağlıdır. Bu ilişki kesme işlemi için $\Delta x / x \le \epsilon$, yuvarlama işlemi için $\Delta x / x \lt \epsilon / 2$ şeklinde ifade olunur. Burada $\epsilon$ sistem (ya da makine) epsilonu olarak bilinir ve  $\epsilon = b^{1 - t}$ olarak ifade edilir. t, mantisteki anlamlı rakam sayısını göstermektedir.  

<b>Örnek:</b> 7 bitlik hayali sayı sistemimiz için makine epsilonu değerini hesaplayalım:

Sistemimizin tabanı 2 olduğundan $b = 2$ 'dir. Mantisteki anlamlı rakam sayısı $t = 3$ 'tür. Bu durumda makine epsilonu $\epsilon = b^{1 - t} = 2^{-2} \rightarrow \epsilon =  0.25$ olarak bulunur. Dolayısı ile kesme işlemi uygulandığında yapılabilecek maksimum göreli hata da bu kadar olacaktır.  Sayılar büyüdükçe kesme işlemi sonucu yapılan hata büyüyor olsa da sayının mutlak değeri de büyüdüğünden göreli hata değeri bu üst sınırın altında kalmaya devam edecektir. Örneğimizde maksimum hata $(0.125000)_{10}$ ile $(0.156250)_{10}$ arasında gerçekleşmektedir. Dolayısı ile hata $(0.156250 – 0.125000) / 0.125000 = 0.25$ olur. 

<b>Önemli Sonuç:</b> Bu problem özellikle iki kayan noktalı sayıyı karşılaştırırken karşımıza çıkar.  Matematiksel olarak birbirine eşitmiş gibi görünen iki ifade kesme ya da yuvarlama nedeniyle birbirinden farklı iki kayan noktalı sayıyla sonuçlanabilir. Doğrusu iki kayan noktalı sayıyı karşılaştırmak yerine, aralarındaki farkın mutlak değerini yeterince küçük seçilmiş bir tolerans değeriyle karşılaştırmak; bu tolerans değerini seçerken ise programı sistem bağımsız hale getirmek üzere makine epsilonundan faydalanmaktır! 

$a$ ve $b$ kayan noktalı sayıları için; $a == b$ ya da $a != b$ yerine $abs(a – b) \gt tolerans $ (örn. $2~\epsilon$) gibi bir karşılaştırma yapmak daha doğrudur.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## Makine Epsilonu ##

Makine epsilonu aşağıdaki basit kodla hesaplanabileceği gibi her sistemin makine epsilionu <i>sys.float_info.epsilon</i> ile de öğrenilebilir.

In [ ]:
epsilon = 1.
while epsilon + 1 > 1:
    epsilon /= 2.
epsilon *= 2 
print("Makine epsilonu", epsilon)

In [ ]:
import sys
print(sys.float_info.epsilon)

7 bitlik hayali sayı sistemi örneğimiz konuyu daha iyi kavratabilmek amacıyla oldukça abartılı limitlere sahiptir. Modern bilgisayarlar kayan noktalı sayı hassasiyeti konusunda çok daha başarılıdır. IEEE standardını takip eden bilgisayarlar sayının işareti için 1 bit, üs için 8 bit,  mantis için 24 bit (toplam 32 bit) kullanırlar. Normalizasyon nedeniyle bu bitlerini birincisi her zaman $1$ olduğundan geriye kalan 23 bitle $10^{-38} - 10^{39}$ arasındaki sayılar ifade edilebilmektedir.

Daha da fazla hassasiyete ihtiyaç duyulduğunda pek çok sistem ek bir hassasiyet seçeneği sunar: <b>Çifte Duyarlılık (Double Precision)</b>. 15-16 ek basamağın sağlandığı bu seçenekle $10^{-308} - 10^{308}$ arasındaki sayıları ifade edilebilecek duyarlılığa kadar inilebilmektedir. 

Tabi bu ek duyarlılık işlemci ve RAM üzerine daha çok yük ve dolayısı ile daha uzun çalışma dezavantajıyla birlikte gelir, bu nedenle uygun yerlerde, dikkatli ve seçilerek kullanılması gereklidir!

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## Aritmetik İşlemlerin Getirdiği Kesme ve Yuvarlama Yanlışları ##

### 1 Toplama ve Çıkarma ### 

Toplama ve çıkarma işlemleri küçük sayının mantisi her iki sayının üssü eşit olacak şekilde düzenlendikten sonra yapılır. 

<b>Örnek 1.</b> $1.5571$ ile $0.4381$ sayılaırnı topluyor olalım. Bu sayılar alt alta yazılırken noktanın aynı yere getirilmesine dikkat ediliyor.

$$ 0.1557~~~~10^1 $$
$$ 0.004381~~~10^1 $$
$$ +----------- $$
$$ 0.160081~~~10^1 $$

Sayı daha az sayıda anlamlı kamak içeren (4) sayı kadar anlamlı rakam içereceğinden ve bunun için kesileceğinden;

$$ 0.1600 x 10^1 $$

şeklinde ifade edilir.

<b>Örnek 2.</b>  $364.1$'den $268.6$'yı çıkarıyor olalım.

$$ ~0.3641~~~~10^2 $$
$$- 0.2686~~~~10^2 $$
$$ ------------ $$
$$ ~0.0955~~~~10^2 $$

Normalizasyon gereği sayı,

$$ 0.9550 x 10^1 $$

şeklinde ifade edilir.

<b>Örnek 3.</b> 

$$ ~0.7642~~~~10^3 $$
$$- 0.7641~~~~10^2 $$
$$ ------------ $$
$$ ~0.0001~~~~10^3 $$

Normalizasyon gereği sayı,

$$ 0.1000 x 10^0 = 0.1$$

şeklinde ifade edilir.

### 2 Çarpma ve Bölme ### 

Çarpma ve bölme işlemleri görece daha kolaydır: Mantisler çarpılır, üsler toplanır! Pek çok sistem ara adımları çift duyarlılıkta saklayarak ilerler.

<b>Örnek: </b>

$$ 0.6313~10^3~x~0.6423~10^{-1} = 0.08754549~10^2 $$

Normalizasyon kesme işlemleri sonrası

$$ 0.8754549~10^1 \Rightarrow 0.8754~10^1$$

### 3 Büyük ve Küçük Sayıyla Toplama Çıkarma ### 

Kesme / yuvarlama nedeniyle bazen işlem yapılmamış gibi bir sonuçla dahi karşılaşılabilir.

$$ 0.4000~~~~10^4 $$
$$ 0.0000001~~~10^4 $$
$$ +----------- $$
$$ 0.4000001~~~10^4 $$

Kesme işlemi sonrası

$$ 0.4000~10^4 $$

In [ ]:
x = 0.000001
toplam = 0.
for i in range(0, 1000000, 1):
    toplam += x
print("Toplam: ", toplam)

### 4 Yakın İki Sayıyı Çıkarma ### 

Birbirlerine çok yakın iki sayı çıkarılmaya çalışıldığında sayıların tam temsil edilememesi ve yuvarlama / kesme işlemi kaynaklı olan, ancak beklenmeyen sorunlarla karşılaşılabilir. Buna iyi bir örnek ikinci dereceden bir denklemin kökleri hesaplanırken karşılaşılabilecek olan aşağıdaki gibi bir sonuçtur.

$$ \frac{-b \pm \sqrt{b^2 - 4~a~c}}{2~a} $$

In [ ]:
from math import sqrt
a = 1.
b = 3000.001
c = 3.
x1 = (-1*b - sqrt(b**2 - 4*a*c))/(2*a)
x2 = (-1*b + sqrt(b**2 - 4*a*c))/(2*a)
print("x1: ", x1)
print("x2: ", x2)

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Python'da Kayan Noktalı Sayılar #

Görüldüğü gibi kayan noktalı sayılar ilgili olarak karşılaşılan en temel sorun onluk sayı sistemindeki bir sayının ikilik sayı sisteminde tam olarak ifade edilememesidir.  Örneğin, $0.1$ sayısının ikilik sayı sistemindeki karşılığı $0.0001100110011001100110011001100110011001100110011...$ 

Python $repr()$ fonksiyonu ve Python promptu kayan noktalı bir sayıyı 17 basamak duyarlıılıkla gösterir. İstenirse sayı ekrana daha büyük bir duyarlılıkla da getirilebilir.

In [ ]:
from math import pi 
print(format(pi, '.12g'))
print(repr(pi))

Gerçekte bu bir ilüzyondur. Zira bu sayının tam bir gösterimini yapabilmek mümkün değildir. Ekrana bindirilen görüntü her zaman belirli duyarlılıkta bir yaklaşımdan ibarettir. Aşağıdaki örnek daha açıklayıcıdır.

In [ ]:
print(.1 + .1 + .1 == .3)
print(round(.1, 1) + round(.1, 1) + round(.1, 1) == round(.3, 1))
print(round(.1 + .1 + .1, 10) == round(.3, 10))

math modülü fonksiyonlarından fsum ise toplama işleminde yuvarlama kaynaklı hataların giderilmesini sağlar.

In [ ]:
from math import fsum
print(sum([.1, .1, .1, .1, .1, .1, .1, .1, .1, .1]))
print(fsum([.1, .1, .1, .1, .1, .1, .1, .1, .1, .1]))

Python'da bir kayan noktalı sayının hangi iki tam sayının oranı olarak ifade edildiğini veren bir metot bulunmaktadır. Kayan sayı nesnelerinin bir metodu olan <i>as_integer_ratio().</i>

In [ ]:
print(3.5.as_integer_ratio())
from math import pi
print(pi.as_integer_ratio())

Bu fonksiyonu kullanarak 0.1 sayısının nasıl temsil edildiğine bakalım. 1/10 değil, çünkü 1/10 ikilik sayı sisteminde tam olarak gösterilemez!

In [ ]:
 0.1.as_integer_ratio()

$fractions$ modülü fonksyonları bu tür sorunların çözümünü kolaylaştırmak konusunda oldukça yardımcı olur. 

In [ ]:
from fractions  import Fraction
Fraction.from_float(0.1)

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Decimal Modülü #

<b>Decimal modülü</b> kayan noktalı sayılarla işlemlerde hızlı ve doğru bir şekilde yuvarlama olanağı sağlayan fonksiyonlara sahiptir. Modül float nesnesine göre bazı önemli avantajlarla gelmektedir.

<b>Decimal</b> insanların elle işlem yapma prensiplerini temel alarak dizayn edilen bir kayan noktalı sayı modeline dayanır (IEEE Standart 854-1987). Bu şekilde bilgisayarın insanların okulda öğrendikleri şekilde işlem yapabilmelerine olanak sağlamış olur. $Decimal$ modülünde sayılar onluk sayı sisteminde temsil edildikleri şekliyle "tam olarak" temsil edilebilirler. $0.1$ gibi sayılar standart float veri türü ile gördüğünüz gibi tam olarak temsil edilememektedir. 

Modül üç kavram üzerine kuruludur: <b>Decimal sayı nesnesi (decimal number)</b>, <b>aritmetik işlemler</b> ve <b>uyarılar (Warnings)</b>. <i>Decimal sayı nesnesi</i> içeriği değiştirilemezdir (immutable). İşareti, mantisi ve üssü ile tanımlıdır. Sayıların sonundaki sıfırlar anlamlı rakam sayısını korumak üzere atılmaz. $Infinity$, $-Infinity$ ve $NaN$ gibi özel türleri de içerir. Aritmetik işlemler için kurallar tanımlıdır ve pek çok yuvarlama opsiyonu sağlanır (<i>ROUND_CEILING, ROUND_DOWN, ROUND_FLOOR, ROUND_HALF_DOWN, ROUND_HALF_EVEN, ROUND_HALF_UP, ROUND_UP ve ROUND_05UP</i>). İşlem sonucuna göre de pek çok uyarı döndürme opsiyonu bulunmaktadır ($InvalidOperation$, $DivisionByZero$, $Inexact$, $Rounded$, $Subnormal$, $Overflow$, $Underflow$ ve $FloatOperation$).

Genel olarak onluk sayı sisteminde ifade edildiği şekilde bir metin nesnesi (string) olarak tanımlanır ve daha sonra `decimal.Decimal` fonksiyonu kullanılarak bir `Decimal` nesnesine dönüştürülür.

In [ ]:
from decimal import *
Decimal("0.1")

Bir kayan noktalı sayıyı da bir `Decimal` dönüştürmek mümkündür. Ancak bu kez sayı amaçlandığı şekilde onluk sayı sisteminde ifade edildiği şekilde değil ikilik sayı sisteminde ifade edilebildiği şekilde onluk sayı sistemine dönüştürülmüş olur.

In [ ]:
Decimal(0.1)

Sayıları ondalık sayı sisteminde olduğu şekilde temsil edebildiğiniz gibi ölçüm duyarlılığı da korunur. Ancak işlemlerde anlamlı rakam sayısı sonuca tam olarak [anlamlı rakamlarla aritmetik kurallarına](Ders01_Hata_Analizi.ipynb#Anlamlı-Rakamlarla-Aritmetik) göre transfer edilmez.

In [ ]:
print(Decimal('0.1') + Decimal('0.1') + Decimal('0.1') == Decimal('0.3'))
print(Decimal('3.40') + Decimal('1.60'))
print(Decimal('0.745')*Decimal('2.2')/Decimal('3.885'))

Decimal modülünde işlem yaparken sisteminiz tarafından sağlanan duyarlılığın üzerine çıkabilirsiniz. Daha fazla bilgi için [bkz](https://docs.python.org/3/library/decimal.html#module-decimal)

In [ ]:
getcontext().prec = 6
print(Decimal(1) / Decimal(7))
getcontext().prec = 28
print(Decimal(1) / Decimal(7))
Decimal('0.1428571428571428571428571429')
print(getcontext()) # limitler

Pek çok uygulama için $getcontext$ fonksiyonu ile mevcut ortama (kontekst) ulaşılarak ayarlar değiştirilebliir. Ancak bazen kullanıcı kendi ortamını (kontekst) yaratmaya ya da birden fazla ortamda işlem yapmaya ihtiyaç duyabilir. $Context()$, $setcontext()$ metodları yeni bir ortam oluşturmak için kullanılabilir. $decimal$ modülü tarafından sağlanan standart ortamlar (kontekstler) ise $BasicContext$ ve $ExtendedContext$'tir. 

In [ ]:
benimortamim = Context(prec=60, rounding=ROUND_HALF_DOWN)
setcontext(benimortamim)
print("Benim Ortamim")
print("1/7 = ", Decimal(1) / Decimal(7))
print("----------------------")
print("Extended Context")
ExtendedContext
setcontext(ExtendedContext)
print("1/7 = ", Decimal(1) / Decimal(7))
print("42 / 0 =", Decimal(42) / Decimal(0))
print("------------------------")
print("Basic Context")
setcontext(BasicContext)
print("42 / 0 = ", Decimal(42) / Decimal(0))

Kontekstlerin problemli durumlar karşısında kullanıcıyı uyarmak üzere uyarı mesajı işaretleri ($flag$) vardır. Bu işaretleri kaldırmadan işlemlere devam edilmez, bunun için <i>clear_flags()</i> metodu kullanılır.

In [ ]:
setcontext(ExtendedContext)
print("355 / 113 = ", Decimal(355) / Decimal(113))
print(getcontext().clear_flags())
print("355 / 113 = ", Decimal(355) / Decimal(113))
print(getcontext())

Burada yapılan bölmenin yaklaşık sonucunun yuvarlandığını ($Rounded$) ve bu nedenle sonucun tam olmadığını ($Inexact$) gösteren bir işaret ($Flag$) bulunmaktadır. 

İstendiğinde bir kontekstin (ortamın) hata mesajı verecek şekilde ayarlanması mümkündür. Bunun için kontekstin traps sözlüğünden faydalanılır.

In [ ]:
setcontext(ExtendedContext)
print("1 / 0 = ", Decimal(1) / Decimal(0))
getcontext().traps[DivisionByZero] = 1
print("1 / 0 = ", Decimal(1) / Decimal(0))

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## Decimal Modülünde Yuvarlama Seçenekleri ##

`Decimal` modülünde yuvarlama işlemleri için `quantize` metodu kullanılır. Herhangi bir yuvarlama stratejisi kullanılabilir ancak varsayılan yöntemde (<i>ROUND_HALF_EVEN</i>) yuvarlamada tıpkı `round` fonksiyonunda olduğu gibi, klasik olarak takip edilen yuvarlama kurallarına uyulur. Ancak bu kez yuvarlamada sayının gösterim şekli esas alınır.

In [ ]:
print(Decimal('1.65').quantize(Decimal('1.0')))
print(Decimal('7.325').quantize(Decimal('.01'), rounding=ROUND_DOWN))
print(Decimal('7.325').quantize(Decimal('1.'), rounding=ROUND_UP))

Son olarak kullanılan yuvarlama kuralı kalıcı hale getirildiğinden varsayılana dönmek için varsayılan kuralın tekrar hatırlatılması gerekir.

In [ ]:
print(Decimal('1.65').quantize(Decimal('1.0')))
print(Decimal('1.65').quantize(Decimal('1.0'), rounding=ROUND_HALF_EVEN))
print(Decimal("2.675").quantize(Decimal("1.00")))

`Decimal` modülünün yuvarlama fonksiyonlarından bazıları klasik yuvarlama stratejilerinden bir miktar farklı çalışmaktadır. Örneğin <i>ROUND_HALF_UP</i> fonksiyonu beklentinin (ve genel kuralın) aksine sayıları 0'dan uzaklatırşacak şekilde yuvarlarken <i>ROUND_HALF_DOWN</i> sayıları 0'a yaklaştıracak şekilde yuvarlar.

In [ ]:
getcontext().rounding = ROUND_UP
print(Decimal("4.42").quantize(Decimal("1.0")))
print(Decimal("-4.42").quantize(Decimal("1.0")))
getcontext().rounding = ROUND_DOWN
print(Decimal("6.28").quantize(Decimal("1.0")))
print(Decimal("-6.28").quantize(Decimal("1.0")))

Bu iki fonksiyonun sondaki rakamın 5 olması durumundaki her iki yöndeki (pozitif ve negatif) davranışları da aynı şekildedir. <i>ROUND_UP</i> 0'dan uzaklaştıracak, <i>ROUND_DOWN</i> 0'a yaklaştıracak şekilde sayıları yuvarlar. <i>ROUND_HALF_UP</i> ve <i>ROUND_HALF_DOWN</i> 'ın davranışları da benzerdir.

In [ ]:
getcontext().rounding = ROUND_HALF_UP
print(Decimal("4.45").quantize(Decimal("1.0")))
print(Decimal("-4.45").quantize(Decimal("1.0")))
getcontext().rounding = ROUND_HALF_DOWN
print(Decimal("6.25").quantize(Decimal("1.0")))
print(Decimal("-6.25").quantize(Decimal("1.0")))

`Decimal` modülündeki <i>ROUND_05UP</i> fonksiyonu ise ilginç bir yuvarlama stratejisi daha sağlar. 

In [ ]:
getcontext().rounding = ROUND_05UP
print(Decimal("3.76").quantize(Decimal("1.0")))
print(Decimal("4.45").quantize(Decimal("1.0")))
print(Decimal("-4.45").quantize(Decimal("1.0")))

Yukarıdaki davranışı itibarı ile strateji her sayıyı 0'a doğru yuvarlar gibi görünmektedir. Ancak aşağıdaki ilk örnekte sayı önce 0'a doğru yuvarlanmaktadır ($1.4$). Ancak bir sonraki sayı 4 olduğu (0 ya da 5 olmadığı) için sayı olduğu gibi bırakılmaktadır. İkinci örnekte ise sayı 0' doğru yuvarlandıktan sonra ($1.5$) 5 ile karşılaşılmakta, bu ise sayının yukarıya yuvarlanmasına neden olmaktadır. Karşılaşılan sayı 0 olduğunda da davranış şekli aynıdır.

In [ ]:
print(Decimal("1.49").quantize(Decimal("1.0")))
print(Decimal("1.51").quantize(Decimal("1.0")))

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Numpy Modülünde Yuvarlama Seçenekleri #

`Numpy` modülündeki `around` fonksiyonu, Python'un `round` fonksiyonuna benzer şekilde çalışır ve tıpkı onun gibi sayıların mükemmel temsil edilememesi sorunundan muzdariptir.

In [ ]:
import numpy as np
np.random.seed(444) #her calismada ayni ciktiyi uretmek icin
dizi = np.random.randn(3, 5)
print(dizi)
yeni_dizi = np.around(dizi, decimals=4)
print(yeni_dizi)

`math` modülündeki `ceil`, `trunc` ve `floor` fonksiyonlarının diziler için çalışan eşlenikleri `numpy` için de vardır.

In [ ]:
print(np.ceil(dizi))
print(np.trunc(dizi))
print(np.floor(dizi))

Sayılardan bazılarının negatif sıfıra ($-0$) yuvarlandığında dikkat ediniz. Negatif 0, bize bu sayının yuvarlandığını ve 0'dan küçük bir sayıdan yuvarlandığını söylemektedir. Bu durum, örneğin suyun sıcaklığı olduğunda onun donma noktasnın altında bir sıcaklığa sahip olduğu konusunda bir fikir verebilir.

Tam sayıya yuvarlamada klasik yuvarlama stratejisi numpy modülünde `rint` fonksiyonu ile sağlanmıştır.

In [ ]:
print(np.rint(dizi))

Diğer yuvarlama seçenekleri numpy'da verilen bu seçenekler kullanılarak kodlanabilir. Numpy modülü `Decimal` modülü ile birlikte kullanılamamaktadır. Yine de istenirse, istenen gösterimdeki metin nesneleri bir liste içinde `Decimal` nesnesine dönüştürüldükten sonra `numpy.array` fonksiyonu ile numpy dizilerine dönüştürülebilir.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Pandas Modülünde Yuvarlama Seçenekleri #

`math` modülündeki `round` ve `numpy` modülündeki `around` fonksiyonlarının `pandas` modülündeki karşılığı da `round` fonksiyonudur ve hem pandas serileri (`pandas.series`) hem de veri çeerçeveleri (`pandas.DataFrame`) üzerinde kullanılabilir.

In [ ]:
import pandas as pd
import numpy as np
np.random.seed(444)
seri = pd.Series(np.random.randn(5))
print(seri)

In [ ]:
print(seri.round(3))

In [ ]:
df = pd.DataFrame(np.random.randn(4, 4), columns=["A", "B", "C", "D"])
print(df)
df.round(2)    

İstenirse her bir sütun (seriye) ayrı bir basamağa da yuvarlanabilir.

In [ ]:
df.round({"A": 1, "B": 2, "C": 3, "D": 0})

In [ ]:
basamak_sayisi = pd.Series([3, 0, 1, 2], index=["A", "B", "C", "D"])
df.round(basamak_sayisi)

`numpy` modülünün `ceil`, `trunc`, `floor` ve `rint` fonksiyonları `pandas` serileri ve dizileri üzerinde de kullanılabilir.

In [ ]:
print(np.ceil(dizi))
print(np.floor(dizi))
print(np.trunc(dizi))
print(np.rint(dizi))

Gerek yuvarlamada, gerekse hata hesaplarında kritik olan tüm kavramalara hakim olup yerli yerince kullanmaktır. Kullanılan gözlemsel / deneysel verinin duyarlılığına bağlı seçimler yapılarak uygun yuvarlama / kesme seçenekleri kullanılmalı; anlamlı rakamlara özen gösterilmelidir. İşlemler ve fonksiyonlar sonucu elde edilen niceliklerin duyarlılıkları (üzerlerindeki belirsizlikler) verilirken işleme giren parametrelerin üzerindeki belirsizlikler dikkate alınmalıdır. Bir sonucun hatası verileriken hatanın türü (standart sapma, standart hata, tahmini hata, uyumlamadan fark karelerin toplamının karekökü (ing. root-mean-square, rms), varyans ...) mutlaka belirtilmeli, verilen niceliğin basamak sayısı ile hatasının basamak sayısnın aynı olmasına özen gösterilmeldir. 

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Kaynaklar #

* Sayı Sistemleri ve Yuvarlama Problemleri: "Numerical Methods for Engineers", 6th ed., Steven C. Chapra, Raymond P. Canale, McGraw Hill, 2009

* Yuvarlama ve Decimal Modülü Konuları: [Real Python](https://realpython.com/python-rounding/), Dan Bader

* Yuvarlama Konusu (round fonksiyonu): [round Fonksiyonu Dokümantasyonu](https://docs.python.org/3/library/functions.html#round)

* [Decimal Modülü Dokümantasyonu](https://docs.python.org/2/library/decimal.html)

* [Kayan Noktalı Sayılarla Aritmetik](http://perso.ens-lyon.fr/jean-michel.muller/goldberg.pdf)

* [Python'da Kayan Noktalı Sayılar](https://docs.python.org/3/tutorial/floatingpoint.html)

* [IEEE-754 Standartları](https://en.wikipedia.org/wiki/IEEE_754)

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)